### This is a script that converts the format of the model (.ckpt/.safetensors)
#### It also converts the .yaml file included with the SD2.x series
#### It can also be saved as fp16 as an option

Run both of the following two codes

In [ ]:
from google.colab import drive 
drive.mount("/content/drive")

In [ ]:
!pip install torch safetensors
!pip install pytorch-lightning
!pip install wget

Replace the following links, etc. with the desired ones and then run the following code

In [ ]:
#@title <font size="-0">Download Models</font>
#@markdown Please specify the model name or download link for Google Drive, separated by commas
#@markdown - If it is the model name on Google Drive, specify it as a relative path to My Drive
#@markdown - If it is a download link, copy the link address by right-clicking and paste it in place of the link below
import shutil
import urllib.parse
import urllib.request
import wget

models = "Specify_the_model_in_this_way_if_the_model_is_on_My_Drive.safetensors, https://huggingface.co./hakurei/waifu-diffusion-v1-4/resolve/main/wd-1-4-anime_e1.ckpt, https://huggingface.co./hakurei/waifu-diffusion-v1-4/resolve/main/wd-1-4-anime_e1.yaml" #@param {type:"string"}
models = [m.strip() for m in models.split(",")]
for model in models:
  if 0 < len(urllib.parse.urlparse(model).scheme): # if model is url
    wget.download(model)
  elif model.endswith((".ckpt", ".safetensors", ".yaml")):
    shutil.copy("/content/drive/MyDrive/" + model, "/content/" + model) # get the model from mydrive
  else:
    print(f"\"{model}\" is not a URL and is also not a file with a proper extension")

In [ ]:
#@title <font size="-0">Convert the Models</font>
#@markdown Specify the models to be converted, separated by commas<br>
#@markdown If nothing is inputted, all loaded models will be converted
import os
import glob
import torch
import safetensors.torch
from functools import partial

models = "wd-1-4-anime_e1.ckpt, wd-1-4-anime_e1.yaml" #@param {type:"string"}
as_fp16 = True #@param {type:"boolean"}
save_directly_to_Google_Drive = True #@param {type:"boolean"}
save_type = ".safetensors" #@param [".safetensors", ".ckpt"]

def convert_yaml(file_name):
  with open(file_name) as f:
    yaml = f.read()
  if save_directly_to_Google_Drive:
    os.chdir("/content/drive/MyDrive")
  is_safe = save_type == ".safetensors"
  yaml = yaml.replace(f"use_checkpoint: {is_safe}", f"use_checkpoint: {not is_safe}")
  if as_fp16:
    yaml = yaml.replace("use_fp16: False", "use_fp16: True")
    file_name = os.path.splitext(file_name)[0] + "-fp16.yaml"
  with open(file_name, mode="w") as f:
    f.write(yaml)
  os.chdir("/content")

if models == "":
  models = [os.path.basename(m) for m in glob.glob(r"/content/*.ckpt") + glob.glob(r"/content/*.safetensors") + glob.glob(r"/content/*.yaml")]
else:
  models = [m.strip() for m in models.split(",")]

for model in models:
  model_name, model_ext = os.path.splitext(model)
  if model_ext == ".yaml":
    convert_yaml(model)
  elif (model_ext != ".safetensors") & (model_ext != ".ckpt"):
    print("The supported formats are only .ckpt, .safetensors, and .yaml\n" + f"\"{model}\" is not a supported format")
  else:
    load_model = partial(safetensors.torch.load_file, device="cpu") if model_ext == ".safetensors" else partial(torch.load, map_location=torch.device("cpu"))
    save_model = safetensors.torch.save_file if save_type == ".safetensors" else torch.save
    # convert model
    with torch.no_grad():
      weights = load_model(model)
      if "state_dict" in weights:
        weights = weights["state_dict"]
      if as_fp16:
        model_name = model_name + "-fp16"
        for key in weights.keys():
          weights[key] = weights[key].half()
      if save_directly_to_Google_Drive:
        os.chdir("/content/drive/MyDrive")
      save_model(weights, model_name + save_type)
      os.chdir("/content")
      del weights

!reset

If you are converting SD2.x series models, etc., be sure to download/convert the accompanying configuration file (a .yaml file with the same name as the model) at the same time.

It can be converted in the same way as the model.

If you run out of memory and crash, you can use a smaller model or a paid high memory runtime.

With the free ~12GB runtime, you can convert models up to ~10GB.

Choose your favorite model from https://huggingface.co./models?other=stable-diffusion or other model link collections